# Reduced 2 Body Problem

We can turn 1 2 body problem into 2 1 body problems 
where one is done from the center of mass frame and the other is done from the reduced mass frame 

In [ ]:
# libaries 

import numpy as np
import sympy as smp 
import matplotlib.pyplot as plt
from scipy.integrate import odeint 
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm

from matplotlib.animation import FFMpegWriter
import matplotlib.animation as animation
plt.style.use("dark_background")


In [ ]:
%matplotlib qt
# %matplotlib inline 

## methods

references: 

https://levelup.gitconnected.com/the-two-body-problem-in-python-6bbe4a0b2f88

https://stackoverflow.com/questions/37146420/saving-matplotlib-animation-as-mp4

In [ ]:
G = 6.67e-20 # km instead of meters 

time = np.arange(0,200,0.8) # made this shorter 

# initial conditions
vmag = np.sqrt(G * (m1 + m2) / np.linalg.norm(r10 - r20)) / 2
m1 = 1e26 
r10 = np.array([0,1000,0]) # intiial array -- cm frame i think # originally 0,0,0
v10 = np.array([-vmag,0,0]) # this baby be moving through space

# initial conditions 2 

m2 = 2e26 
r20 = np.array([0,-500,0]) # originally 3000,0,0
v20 = np.array([vmag * m1/m2,0,0])

y0 = np.concatenate((r10,r20,v10,v20))
np.sqrt(G * (m1 + m2) / np.linalg.norm(r10 - r20))

In [ ]:
# solving 

def solve(y, t, G, m1, m2):
    r1, r2 = y[:3], y[3:6]
    v1, v2 = y[6:9], y[9:12]
    
    r_mag = np.linalg.norm(r2 - r1)
    c0 = np.concatenate((v1,v2)) # dx = vdt 
    c1 =  G * m2 * (r2 - r1)/ r_mag ** 3 # dv = adt
    c2 =  G * m1 * (r1 - r2)/ r_mag ** 3 # dv = adt
    
    return np.concatenate((c0,c1,c2))

y = odeint(solve, y0, time, args = (G, m1,m2))

In [ ]:
r1, r2 = y.T[:3], y.T[3:6] 
rcm = ((m1 * r1) + (m2 * r2)) / (m1 + m2) # defining CM frame 


In [ ]:
metadata = dict(title='test_binary_stars', artist='Matplotlib',comment='hello world!')
writer = FFMpegWriter(fps=15, metadata=metadata)

In [ ]:
fig = plt.figure(dpi=200) # making my figure dpi = dots per inch (determines final resolution)
with writer.saving(fig, "nothing_to_see_here.mp4", dpi=200):

    ax=fig.add_subplot(111,projection="3d")

    x1 = y.T[0]
    y1 = y.T[1]
    z1 = y.T[2]
    x2 = y.T[3]
    y2 = y.T[4]
    z2 = y.T[5]
    
    xcm = rcm[0]
    ycm = rcm[1]
    zcm = rcm[2]
    
    # add CM frame if you want too 
    
    t = time
    line1 = [x1,y1,z1] # this will be the path of each star
    line2 = [x2,y2,z2]
    linecm = [xcm, ycm, zcm]


#     def animate(i):
#         line.set_data(x1[:i],y1[:i])
#         line.set_3d_properties(z1[:i])

#     for i in range(len(t))
    for i in range(len(t)):
        if i % 2 == 0:
            fig.clear()
            ax=fig.add_subplot(111,projection="3d")

            ax.set_xlim(min(min(x1), min(x2)), max(max(x1), max(x2)))
            ax.set_ylim(min(min(y1), min(y2)), max(max(y1), max(y2)))
            ax.set_zlim(min(min(z1), min(z2)), max(max(z1), max(z2)))

            ax.scatter(x1[i], y1[i], z1[i], s = 200, c = 'blue')
            ax.scatter(x2[i], y2[i], z2[i], s = 200, c = 'red')
            ax.scatter(xcm[i], ycm[i], zcm[i], s = 10, c = 'purple')

            ax.plot(line1[0][:i], line1[1][:i], line1[2][:i], lw = 1, color = 'black')
            ax.plot(line2[0][:i], line2[1][:i], line2[2][:i], lw = 1, color = 'black') 
            ax.plot(linecm[0][:i], linecm[1][:i], linecm[2][:i], lw = 1)
            ax.view_init(elev=10., azim= 10 ) # set this to be inclination? 
            plt.draw()
            plt.pause(0.0001)
            writer.grab_frame()

